In [1]:
import requests
import matplotlib.pyplot as plt
from IPython.display import Image
import folium
import pickle
import pandas as pd
from shapely.geometry import Point
import geopandas as gpd
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster
import pyproj

%matplotlib inline

#conda install -c conda-forge folium

## Using the API to pull building permit application data, as well as approved building permit data, that is related to commercial building.

#### First bring in the shapefiles for use later:

In [2]:
council_districts = gpd.read_file('../data/CD/CD.shp')

In [3]:
business_improvement_districts = gpd.read_file('../data/BID/BID.shp')

In [4]:
#check for EPSG 4326
print(council_districts.crs)
print(business_improvement_districts.crs)

epsg:4326
epsg:4326


## Now, permit application data:
https://data.nashville.gov/Licenses-Permits/Building-Permit-Applications/kqff-rxj8

In [5]:
endpoint = 'https://data.nashville.gov/resource/kqff-rxj8.json'

In [6]:
params = {'$select': 'council_district, permit_subtype_description, mapped_location, date_entered',
    '$q': 'office, commercial', 
    '$limit': 50000}
response = requests.get(endpoint, params = params)
response.status_code

200

In [7]:
applications = response.json()
applications = pd.DataFrame(applications)
print(applications.shape)
applications.head(3)

(93, 4)


council_district             permit_subtype_description  \
0               33  General Office, Professional Services   
1               18         Demolition Permit - Commercial   
2               19  General Office, Professional Services   

                                     mapped_location             date_entered  
0  {'latitude': '36.0251', 'longitude': '-86.6159...  2019-11-08T00:00:00.000  
1  {'latitude': '36.141577', 'longitude': '-86.81...  2020-08-12T00:00:00.000  
2  {'latitude': '36.155245', 'longitude': '-86.76...  2018-04-13T00:00:00.000

#### Rename headers, slice out the lat and lon as well as year:

In [8]:
applications.columns = ['Council District', 'Permit Description', 'Location', 'Year']

In [9]:
applications.dropna()

Council District                     Permit Description  \
0                33  General Office, Professional Services   
1                18         Demolition Permit - Commercial   
2                19  General Office, Professional Services   
3                21          Leasing / Sales Office, Other   
4                14  Medical Office, Professional Services   
..              ...                                    ...   
88               29          Leasing / Sales Office, Other   
89               19  General Office, Professional Services   
90               19  General Office, Professional Services   
91               19   General Office, Civic Administration   
92                1                 Warehouse, Storage S-1   

                                             Location                     Year  
0   {'latitude': '36.0251', 'longitude': '-86.6159...  2019-11-08T00:00:00.000  
1   {'latitude': '36.141577', 'longitude': '-86.81...  2020-08-12T00:00:00.000  
2   {'latitude': '36.155245', 'longitude': '-86.76...  2018-04-13T00:00:00.000  
3   {'latitude': '36.150553', 'longitude': '-86.80...  2019-09-06T00:00:00.000  
4   {'latitude': '36.173402', 'longitude': '-86.60...  2019-06-04T00:00:00.000  
..                                                ...                      ...  
88  {'latitude': '36.068505', 'longitude': '-86.63...  2020-12-15T00:00:00.000  
89  {'human_address': '{"address": "1222 DEMONBREU...  2021-01-19T00:00:00.000  
90  {'latitude': '36.14459', 'longitude': '-86.794...  2020-09-24T00:00:00.000  
91  {'latitude': '36.164679', 'longitude': '-86.77...  2020-12-18T00:00:00.000  
92  {'human_address': '{"address": "3696 STEWARTS ...  2020-11-03T00:00:00.000  

[93 rows x 4 columns]

In [10]:
applications.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 93 entries, 0 to 92
Data columns (total 4 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   Council District    93 non-null     object
 1   Permit Description  93 non-null     object
 2   Location            93 non-null     object
 3   Year                93 non-null     object
dtypes: object(4)
memory usage: 3.0+ KB


In [11]:
#bring out year
applications['Year'] = applications['Year'].str.slice(0, 4)

In [12]:
type(applications['Location'][0])

dict

In [13]:
applications['Location'].head().apply(lambda x: x['latitude'])

0      36.0251
1    36.141577
2    36.155245
3    36.150553
4    36.173402
Name: Location, dtype: object

In [14]:
no_lat = []
for ind, val in applications['Location'].iteritems():
    try:
        val['latitude']
    except:
        print(ind, val)
        no_lat.append(ind)

21 {'human_address': '{"address": "2275 MURFREESBORO PIKE 200", "city": "ANTIOCH", "state": "TN", "zip": "37013"}'}
29 {'human_address': '{"address": "413 PORTSDALE DR", "city": "BRENTWOOD", "state": "TN", "zip": "37027"}'}
33 {'human_address': '{"address": "330 23RD AVE N 200", "city": "NASHVILLE", "state": "TN", "zip": "37203"}'}
34 {'human_address': '{"address": "924B2 S DOUGLAS AVE", "city": "NASHVILLE", "state": "TN", "zip": "37204"}'}
52 {'human_address': '{"address": "28 WHITE BRIDGE PIKE 207", "city": "NASHVILLE", "state": "TN", "zip": "37205"}'}
58 {'human_address': '{"address": "1124C OLD HICKORY BLVD", "city": "MADISON", "state": "TN", "zip": "37115"}'}
89 {'human_address': '{"address": "1222 DEMONBREUN ST", "city": "NASHVILLE", "state": "TN", "zip": "37203"}'}
92 {'human_address': '{"address": "3696 STEWARTS LN", "city": "NASHVILLE", "state": "TN", "zip": "37218"}'}


In [15]:
no_lat

[21, 29, 33, 34, 52, 58, 89, 92]

In [16]:
applications = applications.drop(no_lat)

In [17]:
applications['lat'] = applications['Location'].apply(lambda x: x['latitude'])

In [18]:
applications['lon'] = applications['Location'].apply(lambda x: x['longitude'])

In [19]:
applications.head(3)

Council District                     Permit Description  \
0               33  General Office, Professional Services   
1               18         Demolition Permit - Commercial   
2               19  General Office, Professional Services   

                                            Location  Year        lat  \
0  {'latitude': '36.0251', 'longitude': '-86.6159...  2019    36.0251   
1  {'latitude': '36.141577', 'longitude': '-86.81...  2020  36.141577   
2  {'latitude': '36.155245', 'longitude': '-86.76...  2018  36.155245   

          lon  
0  -86.615902  
1  -86.813823  
2  -86.768517

In [20]:
applications = applications.drop(columns = ['Location'])

#### Create a GeoDataFrame:

In [21]:
applications['geometry'] = applications.apply(lambda x: Point((float(x.lon), 
                                                         float(x.lat))), axis=1)
applications.head(3)

Council District                     Permit Description  Year        lat  \
0               33  General Office, Professional Services  2019    36.0251   
1               18         Demolition Permit - Commercial  2020  36.141577   
2               19  General Office, Professional Services  2018  36.155245   

          lon                            geometry  
0  -86.615902  POINT (-86.61590200000001 36.0251)  
1  -86.813823        POINT (-86.813823 36.141577)  
2  -86.768517        POINT (-86.768517 36.155245)

In [22]:
applications_geo = gpd.GeoDataFrame(applications,
                                   crs = business_improvement_districts.crs,
                                   geometry = applications['geometry'])

In [23]:
type(applications_geo)

geopandas.geodataframe.GeoDataFrame

In [24]:
#make ID for choropleth and put it first:
applications_geo['id'] = applications_geo.index.astype(str)

In [25]:
applications_geo = applications_geo[['id', 'Permit Description', 'Year', 'Council District', 'lat', 'lon', 'geometry']]
applications_geo.head()

id                     Permit Description  Year Council District        lat  \
0  0  General Office, Professional Services  2019               33    36.0251   
1  1         Demolition Permit - Commercial  2020               18  36.141577   
2  2  General Office, Professional Services  2018               19  36.155245   
3  3          Leasing / Sales Office, Other  2019               21  36.150553   
4  4  Medical Office, Professional Services  2019               14  36.173402   

          lon                    geometry  
0  -86.615902  POINT (-86.61590 36.02510)  
1  -86.813823  POINT (-86.81382 36.14158)  
2  -86.768517  POINT (-86.76852 36.15525)  
3     -86.801  POINT (-86.80100 36.15055)  
4  -86.602075  POINT (-86.60207 36.17340)

## Now approved permit data: 
https://data.nashville.gov/Licenses-Permits/Building-Permits-Issued/3h5w-q8b7

In [26]:
endpoint = 'https://data.nashville.gov/resource/3h5w-q8b7.json'

In [27]:
params = {'$select': 'council_dist, permit_subtype_description, mapped_location, date_issued',
    '$q': 'office, commercial', 
    '$limit': 50000}
response = requests.get(endpoint, params = params)
response.status_code

200

In [28]:
issued = response.json()
issued = pd.DataFrame(issued)
print(issued.shape)
issued.head(3)

(1875, 4)


council_dist             permit_subtype_description  \
0           26  General Office, Professional Services   
1           25  General Office, Professional Services   
2            6  General Office, Professional Services   

                                     mapped_location              date_issued  
0  {'latitude': '36.088419', 'longitude': '-86.74...  2019-09-18T00:00:00.000  
1  {'human_address': '{"address": "3796 BEDFORD A...  2019-03-21T00:00:00.000  
2  {'latitude': '36.173405', 'longitude': '-86.76...  2019-06-25T00:00:00.000

In [29]:
issued.columns = ['Council District', 'Permit Description', 'Location', 'Year']

In [30]:
issued.dropna()

Council District                      Permit Description  \
0                  26   General Office, Professional Services   
1                  25   General Office, Professional Services   
2                   6   General Office, Professional Services   
3                  21   Medical Office, Professional Services   
4                   4    General Office, Civic Administration   
...               ...                                     ...   
1870               20  Manufacturing, Light Hazardous (H1-H5)   
1871               19   General Office, Professional Services   
1872                2   General Office, Professional Services   
1873                2   General Office, Professional Services   
1874               19           Leasing / Sales Office, Other   

                                               Location  \
0     {'latitude': '36.088419', 'longitude': '-86.74...   
1     {'human_address': '{"address": "3796 BEDFORD A...   
2     {'latitude': '36.173405', 'longitude': '-86.76...   
3     {'latitude': '36.154683', 'longitude': '-86.80...   
4     {'latitude': '36.040754', 'longitude': '-86.76...   
...                                                 ...   
1870  {'latitude': '36.173237', 'longitude': '-86.87...   
1871  {'latitude': '36.163711', 'longitude': '-86.77...   
1872  {'latitude': '36.199826', 'longitude': '-86.80...   
1873  {'latitude': '36.196051', 'longitude': '-86.79...   
1874  {'latitude': '36.153167', 'longitude': '-86.77...   

                         Year  
0     2019-09-18T00:00:00.000  
1     2019-03-21T00:00:00.000  
2     2019-06-25T00:00:00.000  
3     2019-06-03T00:00:00.000  
4     2020-07-06T00:00:00.000  
...                       ...  
1870  2021-03-18T00:00:00.000  
1871  2021-02-05T00:00:00.000  
1872  2021-02-05T00:00:00.000  
1873  2021-02-05T00:00:00.000  
1874  2021-02-05T00:00:00.000  

[1866 rows x 4 columns]

In [31]:
issued.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1875 entries, 0 to 1874
Data columns (total 4 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   Council District    1866 non-null   object
 1   Permit Description  1875 non-null   object
 2   Location            1875 non-null   object
 3   Year                1875 non-null   object
dtypes: object(4)
memory usage: 58.7+ KB


In [32]:
#bring out year
issued['Year'] = issued['Year'].str.slice(0, 4)

In [33]:
type(issued['Location'][0])

dict

In [34]:
no_lat = []
for ind, val in issued['Location'].iteritems():
    try:
        val['latitude']
    except:
        #print(ind, val)
        no_lat.append(ind)

In [35]:
issued = issued.drop(no_lat)

In [36]:
issued['lat'] = issued['Location'].apply(lambda x: x['latitude'])
issued['lon'] = issued['Location'].apply(lambda x: x['longitude'])

In [37]:
issued = issued.drop(columns = ['Location'])

In [38]:
issued['permit_count'] = 1

In [39]:
issued_by_district = issued.groupby(['Council District'])['permit_count'].apply(lambda x : x.astype(int).sum())

In [40]:
issued_by_district = pd.DataFrame(issued_by_district)

In [41]:
issued_by_district.head()

permit_count
Council District              
1                            6
10                          17
11                          15
12                           7
13                          51

In [42]:
issued_by_district.columns(['Council District', 'permit_count'])

TypeError: 'Index' object is not callable

#### Make a GeoDataFrame for Points

In [43]:
issued['geometry'] = issued.apply(lambda x: Point((float(x.lon), 
                                                         float(x.lat))), axis=1)
issued.head(3)

Council District                     Permit Description  Year        lat  \
0               26  General Office, Professional Services  2019  36.088419   
2                6  General Office, Professional Services  2019  36.173405   
3               21  Medical Office, Professional Services  2019  36.154683   

          lon  permit_count                              geometry  
0  -86.748409             1          POINT (-86.748409 36.088419)  
2  -86.763282             1          POINT (-86.763282 36.173405)  
3  -86.804336             1  POINT (-86.80433600000001 36.154683)

In [44]:
issued_geo = gpd.GeoDataFrame(issued,
                                   crs = business_improvement_districts.crs,
                                   geometry = issued['geometry'])

In [45]:
type(issued_geo)

geopandas.geodataframe.GeoDataFrame

#### Make GDF for choropleth:

In [46]:
#make ID for choropleth and put it first:
issued_by_district['id'] = issued_by_district.index.astype(str)

In [47]:
issued_by_district = issued_by_district[['id', 'Council District', 'permit_count']]
issued_by_district.head()

KeyError: "['Council District'] not in index"

In [48]:
issued_by_district_geo = gpd.GeoDataFrame(issued_by_district,
                                   crs = business_improvement_districts.crs,
                                   geometry = issued['geometry'])

In [49]:
issued_by_district = gpd.sjoin( issued_by_district_geo, council_districts, op = 'within')

In [50]:
issued_by_district

Empty GeoDataFrame
Columns: [permit_count, id, geometry, index_right, business_p, council_di, email_addr, first_name, last_name, position]
Index: []

## Bring this all into Folium:

In [51]:
#basemap (used state cap. for the lat/long)
base = folium.Map(location = [36.165096, -86.783637], zoom_start = 10.49, control_scale = True)

#choropleth of application density:
#folium.Choropleth(geo_data = applications_geo,
            #     name = 'Commercial Office Permit Application Density',
               #  data = applications_geo,
               #  columns['id', ''])
            
#create cluster with applications
marker_cluster = MarkerCluster(name = 'Permit Applications').add_to(base)

for row_index, row_values in applications_geo.iterrows():
        loc = row_values['lat'], row_values['lon']
        pop = str(row_values['Permit Description'])
        icon = folium.Icon(color = 'red', prefix = 'fa')
        marker = folium.Marker(location = loc,
                              popup = pop,
                              icon = icon)
        marker.add_to(marker_cluster)
        
#create cluster with issued
marker_cluster = MarkerCluster(name = 'Issued Permits').add_to(base)

for row_index, row_values in issued_geo.iterrows():
        loc = row_values['lat'], row_values['lon']
        pop = str(row_values['Permit Description'])
        icon = folium.Icon(color = 'red', prefix = 'fa')
        marker = folium.Marker(location = loc,
                              popup = pop,
                              icon = icon)
        marker.add_to(marker_cluster)
        
#add business improvement district polygons
folium.GeoJson(business_improvement_districts, name = 'Business Improvement Districts').add_to(base)

#add council district polygons
folium.GeoJson(council_districts, name = 'Council Districts').add_to(base)

#enable layer control
folium.LayerControl().add_to(base)

In [52]:
base